In [1]:
import os
from os.path import join
import numpy as np
import pandas as pd
import pickle
from sklearn import metrics


In [2]:
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier

In [3]:
RANDOM_STATE = 64
WINDOW_SIZE = 80

In [4]:
clean_data_path = r"C:\Users\ke4\Desktop\Goznak_ML_Tasks\train\train\clean"
noisy_data_path = r"C:\Users\ke4\Desktop\Goznak_ML_Tasks\train\train\noisy"

In [6]:
clean_data_path_val = r"C:\Users\ke4\Desktop\Goznak_ML_Tasks\val\clean"
noisy_data_path_val = r"C:\Users\ke4\Desktop\Goznak_ML_Tasks\val\noisy"

In [5]:
clean_data = []
for folder in os.listdir(clean_data_path):
    for file in os.listdir(join(clean_data_path, folder)):
        data = np.load(join(clean_data_path, folder, file))
        clean_data.append(data)
        
noisy_data = []
for folder in os.listdir(noisy_data_path):
    for file in os.listdir(join(noisy_data_path, folder)):
        data= np.load(join(noisy_data_path, folder, file))
        noisy_data.append(data)

In [8]:
clean_data_val = []
for folder in os.listdir(clean_data_path_val):
    for file in os.listdir(join(clean_data_path_val, folder)):
        data = np.load(join(clean_data_path_val, folder, file))
        clean_data_val.append(data)
        
noisy_data_val = []
for folder in os.listdir(noisy_data_path_val):
    for file in os.listdir(join(noisy_data_path_val, folder)):
        data= np.load(join(noisy_data_path_val, folder, file))
        noisy_data_val.append(data)

In [46]:
import plotly.express as px

In [49]:
px.imshow(noisy_data[0].T)

In [50]:
px.imshow(clean_data[0].T)


In [9]:
def divide_windows(features, labels, window_size, step_factor):
    step = int(window_size * step_factor)
    new_features, new_labels = list(), list()
    for i in range(0, features.shape[0] - window_size + 1, step):
        if len(set(labels[i:i + window_size])) != 1:
            continue
        new_features.append([features[i:i + window_size, j] for j in range(features.shape[1])])
        new_labels.append(labels[i])
    return np.array(new_features), np.array(new_labels)

In [10]:
def concat_by_channels(features, labels):
    return features.reshape(features.shape[0], features.shape[1] * features.shape[2]), labels

In [11]:
def accuracy(clf, X_train, y_train, X_val, y_val):
    print(clf)
    print("Доля правильных ответов классификатора на обучающей выборке:", 
    round(clf.score(X_train, y_train), 2)*100,'%')
    print("Доля правильных ответов классификатора на валидационной выборке:", 
    round(clf.score(X_val, y_val), 2)*100,'%')
    print('-------------------------')

In [27]:
def get_predict(meg, clf):
    window_size = 80
    step_factor = 1
    step = int(window_size * step_factor)
    new_features = list()
    for i in range(0, meg.shape[0] - window_size + 1, step):
        new_features.append([meg[i:i + window_size, j] for j in range(meg.shape[1])])
    wind_feature = np.array(new_features)
    
    test = wind_feature.reshape(wind_feature.shape[0], wind_feature.shape[1] * wind_feature.shape[2])
    
    predict_wind = []
    for wind in test:
        predict_wind.append(clf.predict(wind.reshape(1, -1)))
        
    if np.mean(predict_wind)>0.5:
        return 1
    else:
        return 0

Одна запись - это времянной ряд. Первая размерность - длинна записи, вторая - признаки (спектр??).


In [12]:
print(noisy_data[0].shape, noisy_data[1].shape)

(966, 80) (658, 80)


Поскольку длинны у записей разные не получиться классифицировать весь ряд, будем бить на окна и классифицировать окна, далее как понять что запись зашумлена?
1) Считаем среднее предсказание окон у записи, если их среднее > 0.5 - запись зашумлена.

In [13]:
df = pd.DataFrame(clean_data[0])
df['class']=1
df

0         1         2         3         4         5         6  \
0    0.641113  0.611328  0.542969  0.342529  0.269043  0.435547  0.411621   
1    0.667969  0.598633  0.565918  0.470703  0.474609  0.525391  0.439697   
2    0.638672  0.570312  0.587402  0.535645  0.486816  0.507324  0.504883   
3    0.629883  0.545410  0.511230  0.456543  0.474854  0.465820  0.496338   
4    0.684082  0.593750  0.436768  0.395996  0.514160  0.623047  0.498047   
..        ...       ...       ...       ...       ...       ...       ...   
961  0.672852  0.602539  0.547852  0.480713  0.449219  0.407471  0.548828   
962  0.667969  0.607910  0.640137  0.537598  0.451660  0.471924  0.572266   
963  0.674805  0.618164  0.655273  0.528809  0.490479  0.467529  0.503418   
964  0.628418  0.572754  0.570801  0.462646  0.456543  0.526855  0.447754   
965  0.529785  0.510254  0.471191  0.273438  0.406250  0.418701  0.503418   

            7         8         9  ...        71        72        73  \
0    0.479248  0.488281  0.412109  ... -0.390869 -0.393555 -0.343750   
1    0.451660  0.390137  0.353027  ... -0.381104 -0.379150 -0.361084   
2    0.484863  0.271240  0.342285  ... -0.359619 -0.341797 -0.404297   
3    0.421631  0.274170  0.385254  ... -0.372559 -0.361816 -0.418701   
4    0.416748  0.268555  0.323730  ... -0.358398 -0.394043 -0.415771   
..        ...       ...       ...  ...       ...       ...       ...   
961  0.441406  0.213623  0.216309  ... -0.365967 -0.288086 -0.328125   
962  0.450195  0.210083  0.256104  ... -0.314941 -0.282471 -0.310791   
963  0.280762  0.159180  0.224609  ... -0.307617 -0.279297 -0.312988   
964  0.288818  0.084106  0.332764  ... -0.283203 -0.286621 -0.286621   
965  0.388672  0.080688  0.384766  ... -0.220093 -0.214600 -0.239502   

           74        75        76        77        78        79  class  
0   -0.367676 -0.472168 -0.381104 -0.387207 -0.420898 -0.335693      1  
1   -0.363281 -0.396484 -0.363525 -0.353516 -0.354248 -0.314453      1  
2   -0.375732 -0.344971 -0.341797 -0.362061 -0.368408 -0.315674      1  
3   -0.397217 -0.373535 -0.347900 -0.366699 -0.395264 -0.357178      1  
4   -0.387939 -0.351807 -0.407959 -0.357178 -0.374512 -0.350830      1  
..        ...       ...       ...       ...       ...       ...    ...  
961 -0.247803 -0.221436 -0.273682 -0.164673 -0.172852 -0.262451      1  
962 -0.285156 -0.212769 -0.182861 -0.172974 -0.171631 -0.230347      1  
963 -0.294189 -0.258545 -0.202637 -0.247070 -0.219604 -0.226685      1  
964 -0.313232 -0.311768 -0.265869 -0.228027 -0.183716 -0.198608      1  
965 -0.280273 -0.288086 -0.302246 -0.209961 -0.204346 -0.220947      1  

[966 rows x 81 columns]

In [14]:
df_clean = pd.DataFrame(np.vstack(clean_data))
df_clean['class']=0
df_noisy = pd.DataFrame(np.vstack(noisy_data))
df_noisy['class']=1
df_total = pd.concat([df_clean,df_noisy])
df_total.reset_index(drop=True, inplace=True)

df_clean_val = pd.DataFrame(np.vstack(clean_data_val))
df_clean_val['class']=0
df_noisy_val = pd.DataFrame(np.vstack(noisy_data_val))
df_noisy_val['class']=1
df_total_val = pd.concat([df_clean_val,df_noisy_val])
df_total_val.reset_index(drop=True, inplace=True)


In [19]:
wind_feature, wind_label=divide_windows(df_total.drop('class', axis=1).values,
                                        labels = df_total['class'],
                                        window_size=WINDOW_SIZE,
                                        step_factor=1)

In [20]:
wind_feature_val, wind_label_val=divide_windows(df_total_val.drop('class', axis=1).values,
                                                labels = df_total_val['class'],
                                                window_size=WINDOW_SIZE,
                                                step_factor=1)

In [21]:
wind_feature.shape

(227681, 80, 80)

In [22]:
wind_label.shape

(227681,)

In [23]:
X_train, y_train = concat_by_channels(wind_feature, wind_label)
X_val, y_val = concat_by_channels(wind_feature_val, wind_label_val)

In [18]:
X_train.shape

(227681, 6400)

In [19]:
y_train.shape

(227681,)

In [20]:
X_val.shape

(37768, 6400)

In [21]:
y_val.shape

(37768,)

In [25]:
tree = DecisionTreeClassifier(random_state=RANDOM_STATE)

log_reg = LogisticRegression(n_jobs=-1,random_state=RANDOM_STATE)

rnd_for = RandomForestClassifier(n_jobs=-1,random_state=RANDOM_STATE)


In [26]:
tree.fit(X_train, y_train)
with open("models/tree.pkl", "wb") as f:
    pickle.dump(tree, f)
print('tree train finished______')

log_reg.fit(X_train, y_train)
with open("models/log_reg.pkl", "wb") as f:
    pickle.dump(tree, f)
print('log_reg train finished______')

rnd_for.fit(X_train, y_train)
with open("models/rnd_for.pkl", "wb") as f:
    pickle.dump(rnd_for, f)
print('rnd_for train finished______')

tree train finished______
log_reg train finished______
rnd_for train finished______


In [28]:
accuracy(tree, X_train, y_train, X_val, y_val)
accuracy(log_reg, X_train, y_train, X_val, y_val)
accuracy(rnd_for, X_train, y_train, X_val, y_val)

DecisionTreeClassifier(random_state=64)
Доля правильных ответов классификатора на обучающей выборке: 100.0 %
Доля правильных ответов классификатора на валидационной выборке: 85.0 %
-------------------------
LogisticRegression(n_jobs=-1, random_state=64)
Доля правильных ответов классификатора на обучающей выборке: 86.0 %
Доля правильных ответов классификатора на валидационной выборке: 84.0 %
-------------------------
RandomForestClassifier(n_jobs=-1, random_state=64)
Доля правильных ответов классификатора на обучающей выборке: 100.0 %
Доля правильных ответов классификатора на валидационной выборке: 92.0 %
-------------------------


In [17]:
with open("models/tree.pkl", "rb") as f:
    tree = pickle.load(f)
# with open("models/log_reg.pkl", "rb") as f:
#     log_reg = pickle.load(f)
with open("models/rnd_for.pkl", "rb") as f:
    rnd_for = pickle.load(f)

In [29]:
# более правильная оценка лучшего алгоритма
y_pred_0 = []
y_pred_1 = []
y_true_0 = []
y_true_1 = []
k=0
for clean_meg in clean_data_val:
    k+=1
    print(k)
    pred = get_predict(clean_meg, rnd_for)
    y_pred_0.append(pred)
    y_true_0.append(0)
    
for noisy_meg in noisy_data_val:
    pred = get_predict(noisy_meg, rnd_for)
    y_pred_1.append(pred)
    y_true_1.append(1)

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277


1862
1863
1864
1865
1866
1867
1868
1869
1870
1871
1872
1873
1874
1875
1876
1877
1878
1879
1880
1881
1882
1883
1884
1885
1886
1887
1888
1889
1890
1891
1892
1893
1894
1895
1896
1897
1898
1899
1900
1901
1902
1903
1904
1905
1906
1907
1908
1909
1910
1911
1912
1913
1914
1915
1916
1917
1918
1919
1920
1921
1922
1923
1924
1925
1926
1927
1928
1929
1930
1931
1932
1933
1934
1935
1936
1937
1938
1939
1940
1941
1942
1943
1944
1945
1946
1947
1948
1949
1950
1951
1952
1953
1954
1955
1956
1957
1958
1959
1960
1961
1962
1963
1964
1965
1966
1967
1968
1969
1970
1971
1972
1973
1974
1975
1976
1977
1978
1979
1980
1981
1982
1983
1984
1985
1986
1987
1988
1989
1990
1991
1992
1993
1994
1995
1996
1997
1998
1999
2000


In [35]:
rf_accuracy = metrics.accuracy_score(y_pred_0+y_pred_1, y_true_0+y_true_1)  
print('Доля правильно классифицированных валидационных записей: {}%'.format(rf_accuracy*100))


Доля правильно классифицированных валидационных записей: 93.975%
